In [1]:
import pandas as pd
from sklearn.preprocessing import LabelEncoder
import numpy as np
from sklearn.model_selection import train_test_split, RandomizedSearchCV
from sklearn.metrics import r2_score, mean_squared_error
from tqdm import tqdm
from datetime import datetime
import pytz
import json
import joblib 
import os
import optuna

/home/carolima/.local/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Load the dataset after the exploratory data analysis
challenge_set_updated = pd.read_csv("./data/challenge_set_updated_v9_median.csv")
submission_set = pd.read_csv("./data/submission_set.csv")
submission_set_updated = pd.read_csv("./data/submission_set_updated_v9_median.csv")



In [3]:
# If necessary change this part to test the model before the training process
df = challenge_set_updated.iloc[:,:]
# df = challenge_set_updated.sample(frac=0.001)

# Separating features and target variable
X = df.drop('tow', axis=1)
y = df['tow']



In [4]:
import pandas as pd
from sklearn.preprocessing import LabelEncoder

# Handle categorical columns by Label Encoding
label_encoder = LabelEncoder()

# Specify the columns that are categorical
categorical_cols = ['adep', 'ades', 'aircraft_type', 'wtc', 'airline', 'offblock_season', 
                    'flight_duration_category', 'adep_region', 'ades_region', 'flight_direction', 
                    'Manufacturer', 'Model_FAA', 'Physical_Class_Engine', 'FAA_Weight']

# Convert these categorical columns into numerical form using Label Encoding
for col in categorical_cols:
    X[col] = label_encoder.fit_transform(X[col])

# Now, you can proceed with training LightGBM with this processed data


In [5]:
import lightgbm as lgb
from lightgbm import early_stopping, log_evaluation
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, r2_score
import numpy as np
import optuna

# Split the data into training and test sets
X_train_full, X_test, y_train_full, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
X_train, X_val, y_train, y_val = train_test_split(X_train_full, y_train_full, test_size=0.2, random_state=42)

# Define the objective function for Optuna hyperparameter optimization
def objective(trial):
    # Suggest values for the hyperparameters to be optimized
    params = {
        'objective': 'regression',
        'metric': 'rmse',  # Use RMSE as the evaluation metric
        'random_state': 42,
        'n_estimators': 1_000_000,  # Set a high value to allow early stopping
        'learning_rate': trial.suggest_float('learning_rate', 1e-3, 0.1, log=True),
        'max_depth': trial.suggest_int('max_depth', 3, 15),
        'min_child_weight': trial.suggest_int('min_child_weight', 1, 10),
        'subsample': 1.0,
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.4, 1.0),
        'reg_alpha': trial.suggest_float('reg_alpha', 1e-4, 1.0, log=True),
        'reg_lambda': trial.suggest_float('reg_lambda', 1e-4, 1.0, log=True),
        'n_jobs': -1,  # Use all available CPU cores
        'device_type': 'gpu',  # Use GPU for training
        'gpu_platform_id': 0,  # GPU platform ID (if you have multiple GPUs, change accordingly)
        'gpu_device_id': 0  # GPU device ID
    }
    
    # Initialize the LightGBM regressor with the suggested parameters
    model = lgb.LGBMRegressor(**params)
    
    # Train the model with early stopping using callbacks
    model.fit(
        X_train, y_train,
        eval_set=[(X_val, y_val)],
        eval_metric='rmse',
        callbacks=[early_stopping(stopping_rounds=20), log_evaluation(100)]
    )
    
    # Make predictions and calculate the RMSE on the validation set
    preds = model.predict(X_val)
    rmse = np.sqrt(mean_squared_error(y_val, preds))
    
    return rmse

# Start the Optuna study
study = optuna.create_study(direction='minimize')  # Minimize the RMSE
study.optimize(objective, n_trials=50)  # Adjust the number of trials as necessary

# Display the best hyperparameters found
print(f"Best trial: {study.best_trial.params}")

# Train the final model with the best parameters
best_params = study.best_trial.params
best_model = lgb.LGBMRegressor(
    **best_params,
    objective='regression',
    random_state=42,
    n_estimators=1_000_000,
    n_jobs=-1,
    device_type='gpu',  # GPU training
    gpu_platform_id=0,
    gpu_device_id=0
)

# Train the model with LightGBM’s categorical feature handling
best_model.fit(
    X_train, y_train,
    eval_set=[(X_val, y_val)],
    eval_metric='rmse',
    categorical_feature=categorical_cols,  # LightGBM handles these as categorical
    callbacks=[early_stopping(stopping_rounds=20), log_evaluation(100)]
)

# Update the n_estimators parameter with the best number of iterations found
best_params['n_estimators'] = best_model.best_iteration_

# Evaluate the model on the test set
y_pred = best_model.predict(X_test)
r2 = r2_score(y_test, y_pred)
rmse = np.sqrt(mean_squared_error(y_test, y_pred))

print(f"Best Model Performance - R^2 Score: {r2:.4f}, RMSE: {rmse:.4f}")
print(f"Updated best_params: {best_params}")


[I 2024-09-24 15:24:44,954] A new study created in memory with name: no-name-92784243-b0c4-49ad-800f-753122d2c1e8


[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 12511
[LightGBM] [Info] Number of data points in the train set: 235756, number of used features: 80
[LightGBM] [Info] Using requested OpenCL platform 0 device 0
[LightGBM] [Info] Using GPU Device: NVIDIA RTX A4500, Vendor: NVIDIA Corporation
[LightGBM] [Info] Compiling OpenCL Kernel with 256 bins...


1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.
1 warning generated.


[LightGBM] [Info] GPU programs have been built
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 69 dense feature groups (16.19 MB) transferred to GPU in 0.010808 secs. 1 sparse feature groups
[LightGBM] [Info] Start training from score 79499.123553
Training until validation scores don't improve for 20 rounds
[100]	valid_0's rmse: 43527.8
[200]	valid_0's rmse: 35780.5
[300]	valid_0's rmse: 29483.8
[400]	valid_0's rmse: 24337.6
[500]	valid_0's rmse: 20153.8
[600]	valid_0's rmse: 16761.5
[700]	valid_0's rmse: 14028.4
[800]	valid_0's rmse: 11821.6
[900]	valid_0's rmse: 10055.2
[1000]	valid_0's rmse: 8651.38
[1100]	valid_0's rmse: 7543.8
[1200]	valid_0's rmse: 6675.52
[1300]	valid_0's rmse: 6007.55
[1400]	valid_0's rmse: 5495.83
[1500]	valid_0's rmse: 5110.89
[1600]	valid_0's rmse: 4816.95
[1700]	valid_0's rmse: 4598.7
[1800]	valid_0's rmse: 4431.01
[1900]	valid_0's rmse: 4300.27
[2000]	valid_0's rmse: 4200.93
[2100]	valid_0's rmse: 4123.18
[2200]	valid_0's rmse: 4061.68
[

[I 2024-09-24 15:32:18,425] Trial 0 finished with value: 2852.000978772471 and parameters: {'learning_rate': 0.002007966579251119, 'max_depth': 6, 'min_child_weight': 9, 'colsample_bytree': 0.6014286059945357, 'reg_alpha': 0.00710022140905114, 'reg_lambda': 0.006241451916495173}. Best is trial 0 with value: 2852.000978772471.


...

[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 12511
[LightGBM] [Info] Number of data points in the train set: 235756, number of used features: 80
[LightGBM] [Info] Using requested OpenCL platform 0 device 0
[LightGBM] [Info] Using GPU Device: NVIDIA RTX A4500, Vendor: NVIDIA Corporation
[LightGBM] [Info] Compiling OpenCL Kernel with 256 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 69 dense feature groups (16.19 MB) transferred to GPU in 0.007199 secs. 1 sparse feature groups
[LightGBM] [Info] Start training from score 79499.123553
Training until validation scores don't improve for 20 rounds
[100]	valid_0's rmse: 27843
[200]	valid_0's rmse: 15090.5
[300]	valid_0's rmse: 8810.37
[400]	valid_0's rmse: 5922.94
[500]	valid_0's rmse: 4722.23
[600]	valid_0's rmse: 4236.33
[700]	valid_0's rmse: 4006.58
[800]	valid_0's rmse: 3878.08
[900]	valid_0's rmse: 3791.12
[1000]	valid_0's rmse: 3724.41

[I 2024-09-24 17:40:16,215] Trial 48 finished with value: 2817.3512421767455 and parameters: {'learning_rate': 0.0066174244236376295, 'max_depth': 12, 'min_child_weight': 5, 'colsample_bytree': 0.4017430687466923, 'reg_alpha': 0.11245225128156415, 'reg_lambda': 0.00012488438035401564}. Best is trial 37 with value: 2793.2924468770148.


[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 12511
[LightGBM] [Info] Number of data points in the train set: 235756, number of used features: 80
[LightGBM] [Info] Using requested OpenCL platform 0 device 0
[LightGBM] [Info] Using GPU Device: NVIDIA RTX A4500, Vendor: NVIDIA Corporation
[LightGBM] [Info] Compiling OpenCL Kernel with 256 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 69 dense feature groups (16.19 MB) transferred to GPU in 0.006521 secs. 1 sparse feature groups
[LightGBM] [Info] Start training from score 79499.123553
Training until validation scores don't improve for 20 rounds
[100]	valid_0's rmse: 16314.7
[200]	valid_0's rmse: 6469.47
[300]	valid_0's rmse: 4372.94
[400]	valid_0's rmse: 3932.49
[500]	valid_0's rmse: 3763.88
[600]	valid_0's rmse: 3655.63
[700]	valid_0's rmse: 3567.95
[800]	valid_0's rmse: 3500.27
[900]	valid_0's rmse: 3448.85
[1000]	valid_0's rmse: 3405.

[I 2024-09-24 17:41:21,846] Trial 49 finished with value: 2832.556703880489 and parameters: {'learning_rate': 0.012248324328465414, 'max_depth': 15, 'min_child_weight': 6, 'colsample_bytree': 0.5601878811897215, 'reg_alpha': 0.4470669579102425, 'reg_lambda': 0.0012389568779641264}. Best is trial 37 with value: 2793.2924468770148.


Best trial: {'learning_rate': 0.008615745773089515, 'max_depth': 13, 'min_child_weight': 8, 'colsample_bytree': 0.5613054637565795, 'reg_alpha': 0.5342775946980672, 'reg_lambda': 0.02861208458090201}
[LightGBM] [Info] This is the GPU trainer!!
[LightGBM] [Info] Total Bins 12628
[LightGBM] [Info] Number of data points in the train set: 235756, number of used features: 80
[LightGBM] [Info] Using requested OpenCL platform 0 device 0
[LightGBM] [Info] Using GPU Device: NVIDIA RTX A4500, Vendor: NVIDIA Corporation
[LightGBM] [Info] Compiling OpenCL Kernel with 256 bins...
[LightGBM] [Info] GPU programs have been built
[LightGBM] [Info] Size of histogram bin entry: 8
[LightGBM] [Info] 69 dense feature groups (16.19 MB) transferred to GPU in 0.007157 secs. 1 sparse feature groups
[LightGBM] [Info] Start training from score 79499.123553
Training until validation scores don't improve for 20 rounds
[100]	valid_0's rmse: 22906.7	valid_0's l2: 5.24718e+08
[200]	valid_0's rmse: 10579.3	valid_0's l2

In [6]:
# Save R², RMSE, and hyperparameters
results = {
    'R2': float(r2),
    'RMSE': float(rmse),
    'Best Parameters': {key: (int(value) if isinstance(value, np.integer) else float(value)
                              if isinstance(value, np.floating) else value)
                        for key, value in best_params.items()}
}

# Set timezone to São Paulo (UTC-3)
saopaulo_tz = pytz.timezone('America/Sao_Paulo')
timestamp = datetime.now(saopaulo_tz).strftime('%Y%m%d_%H%M%S')

# Define logs directory, and create them if they don't exist
logs_dir = 'logs'
os.makedirs(logs_dir, exist_ok=True)

# Define file paths within the respective directories
results_file = os.path.join(logs_dir, f'model_results_{timestamp}.txt')

# Save the results to a TXT file
with open(results_file, 'w') as file:
    file.write(f"R2: {results['R2']}\n")
    file.write(f"RMSE: {results['RMSE']}\n")
    file.write("Best Parameters:\n")
    for param, value in results['Best Parameters'].items():
        file.write(f"  {param}: {value}\n")

print(f"Results saved to {results_file}")

Results saved to logs/model_results_20240924_181401.txt


In [7]:
# Display evaluation metrics
print(f"Final Model Performance - R^2 Score: {r2:.4f}, RMSE: {rmse:.4f}")

Final Model Performance - R^2 Score: 0.9973, RMSE: 2762.0350


In [8]:
# Define models directory, and create them if they don't exist
models_dir = 'models'
os.makedirs(models_dir, exist_ok=True)



# Train the final model using the full training+validation+test set with the optimal n_estimators
final_model = lgb.LGBMRegressor(**best_params, objective='regression', random_state=42, n_jobs=-1)

# Train the model on the entire dataset (X and y)
final_model.fit(X, y)

print("Final model trained successfully using all available data.")

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.010149 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 12517
[LightGBM] [Info] Number of data points in the train set: 368371, number of used features: 80
[LightGBM] [Info] Start training from score 79511.807630
Final model trained successfully using all available data.


In [9]:
# Define file paths within the respective directories
model_file = os.path.join(models_dir, f'trained_model_{timestamp}.joblib')

# Save the trained model to a file in the models folder
joblib.dump(final_model, model_file)
print(f"Model saved to {model_file}")

Model saved to models/trained_model_20240924_181401.joblib


In [14]:

# Impute missing values for categorical columns by filling with a placeholder
categorical_cols = [
    'adep', 'ades', 'aircraft_type', 'wtc', 'airline', 'offblock_season',
    'flight_duration_category', 'adep_region', 'ades_region', 'flight_direction',
    'Manufacturer', 'Model_FAA', 'Physical_Class_Engine', 'FAA_Weight'
]

for col in categorical_cols:
    submission_set_updated[col].fillna('unknown', inplace=True)

# Impute missing values for numerical columns by filling with the median
numerical_cols = submission_set_updated.select_dtypes(include=[np.number]).columns

for col in numerical_cols:
    submission_set_updated[col].fillna(submission_set_updated[col].median(), inplace=True)


# Check the lengths of both DataFrames
len_features = len(submission_set_features)
len_submission = len(submission_set)

# If they do not match, trim the submission_set
if len_features < len_submission:
    submission_set = submission_set.iloc[:len_features]

# Now you can safely assign the predictions
submission_set['tow'] = final_model.predict(submission_set_features)

# Inspect the result
print(submission_set.head())



/tmp/ipykernel_714894/1446572917.py:9: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  submission_set_updated[col].fillna('unknown', inplace=True)
/tmp/ipykernel_714894/1446572917.py:15: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inpl

   flight_id        date                          callsign  adep  \
0  248753821  2022-01-01  3b3de0f3ad0ee192513995c02f7bf7cf  LTFJ   
1  248753822  2022-01-01  e06dd03d4a879ca37d9e18c1bd7cad16  EBBR   
2  248754498  2022-01-01  2d3b1c962c78c4ebeef11bcd51b9e94c  KMIA   
3  248757623  2022-01-01  81564432d3ee97c4bdf4cd8f006753dc  EGCN   
4  248763603  2022-01-01  84be079d7e660db105d91f600b4b3d59  EIDW   

                name_adep country_code_adep  ades        name_ades  \
0  Istanbul Sabiha Gokcen                TR  LFLL             Lyon   
1                Brussels                BE  KJFK     New York JFK   
2                   Miami                US  EGLL  London Heathrow   
3     Doncaster Sheffield                GB  LEAL         Alicante   
4                  Dublin                IE  LFLL             Lyon   

  country_code_ades  actual_offblock_time          arrival_time aircraft_type  \
0                FR  2022-01-01T09:44:00Z  2022-01-01T12:48:33Z          B738   
1       

/tmp/ipykernel_714894/1446572917.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  submission_set['tow'] = final_model.predict(submission_set_features)


In [15]:
submission_set['tow'].describe()


count    105791.000000
mean      81346.714842
std       52364.128528
min       24517.156296
25%       57540.462452
50%       65405.003353
75%       74975.848185
max      322494.875467
Name: tow, dtype: float64

In [16]:
challenge_set_updated['tow'].describe()


count    368371.000000
mean      79511.807653
std       53280.808626
min       14944.000000
25%       55836.000000
50%       63852.000000
75%       73756.000000
max      351327.000000
Name: tow, dtype: float64

In [17]:
# Define the submissions directory and create it if it doesn't exist
submissions_dir = 'submissions'
os.makedirs(submissions_dir, exist_ok=True)

# Save the submission with a timestamp in the filename
submission_file = os.path.join(submissions_dir, f"submission_{timestamp}.csv")
submission_set.to_csv(submission_file, index=False)